In [1]:
import pandas as pd
import os

from helpers import (
    get_combined_df,
    save_final_df_as_jsonl,
    handle_slug_column_mappings,
)

In [2]:
DATA_DIR = "../data"
PROCESSED_DIR = "../processed/"
FACET_DIR = "home_values/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [5]:
data_frames = []

slug_column_mappings = {
    "_tier_0.0_0.33_": "Bottom Tier ZHVI",
    "_tier_0.33_0.67_": "Mid Tier ZHVI",
    "_tier_0.67_1.0_": "Top Tier ZHVI",
    "": "ZHVI",
}

for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        print("processing " + filename)
        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))
        exclude_columns = [
            "RegionID",
            "SizeRank",
            "RegionName",
            "RegionType",
            "StateName",
            "Bedroom Count",
            "Home Type",
        ]

        if "Zip" in filename:
            continue
        if "Neighborhood" in filename:
            continue
        if "City" in filename:
            continue
        if "Metro" in filename:
            continue
        if "County" in filename:
            continue

        if "City" in filename:
            exclude_columns = exclude_columns + ["State", "Metro", "CountyName"]
        elif "Zip" in filename:
            exclude_columns = exclude_columns + [
                "State",
                "City",
                "Metro",
                "CountyName",
            ]
        elif "County" in filename:
            exclude_columns = exclude_columns + [
                "State",
                "Metro",
                "StateCodeFIPS",
                "MunicipalCodeFIPS",
            ]
        elif "Neighborhood" in filename:
            exclude_columns = exclude_columns + [
                "State",
                "City",
                "Metro",
                "CountyName",
            ]

        if "_bdrmcnt_1_" in filename:
            cur_df["Bedroom Count"] = "1-Bedroom"
        elif "_bdrmcnt_2_" in filename:
            cur_df["Bedroom Count"] = "2-Bedrooms"
        elif "_bdrmcnt_3_" in filename:
            cur_df["Bedroom Count"] = "3-Bedrooms"
        elif "_bdrmcnt_4_" in filename:
            cur_df["Bedroom Count"] = "4-Bedrooms"
        elif "_bdrmcnt_5_" in filename:
            cur_df["Bedroom Count"] = "5+-Bedrooms"
        else:
            cur_df["Bedroom Count"] = "All Bedrooms"

        if "_uc_sfr_" in filename:
            cur_df["Home Type"] = "SFR"
        elif "_uc_sfrcondo_" in filename:
            cur_df["Home Type"] = "all homes (SFR/condo)"
        elif "_uc_condo_" in filename:
            cur_df["Home Type"] = "condo"

        cur_df["StateName"] = cur_df["StateName"].astype(str)
        cur_df["RegionName"] = cur_df["RegionName"].astype(str)

        data_frames = handle_slug_column_mappings(
            data_frames, slug_column_mappings, exclude_columns, filename, cur_df
        )


combined_df = get_combined_df(
    data_frames,
    [
        "RegionID",
        "SizeRank",
        "RegionName",
        "RegionType",
        "StateName",
        "Bedroom Count",
        "Home Type",
        "Date",
    ],
)

combined_df

processing City_zhvi_uc_condo_tier_0.33_0.67_sm_sa_month.csv
processing City_zhvi_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing Metro_zhvi_uc_sfrcondo_tier_0.67_1.0_sm_sa_month.csv
processing County_zhvi_uc_sfrcondo_tier_0.67_1.0_sm_sa_month.csv
processing Metro_zhvi_bdrmcnt_2_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing County_zhvi_bdrmcnt_4_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing County_zhvi_uc_sfr_tier_0.33_0.67_sm_sa_month.csv
processing Neighborhood_zhvi_bdrmcnt_4_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing State_zhvi_uc_sfr_tier_0.33_0.67_sm_sa_month.csv
processing County_zhvi_uc_condo_tier_0.33_0.67_sm_sa_month.csv
processing City_zhvi_bdrmcnt_4_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing State_zhvi_bdrmcnt_5_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing Zip_zhvi_bdrmcnt_2_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing City_zhvi_uc_sfrcondo_tier_0.67_1.0_sm_sa_month.csv
processing Zip_zhvi_uc_condo_tier_0.33_0.67_

RegionID  SizeRank RegionName RegionType StateName Bedroom Count  \
0              3        48     Alaska      state       nan     1-Bedroom   
1              3        48     Alaska      state       nan     1-Bedroom   
2              3        48     Alaska      state       nan     1-Bedroom   
3              3        48     Alaska      state       nan     1-Bedroom   
4              3        48     Alaska      state       nan     1-Bedroom   
...          ...       ...        ...        ...       ...           ...   
117907        62        51    Wyoming      state       nan  All Bedrooms   
117908        62        51    Wyoming      state       nan  All Bedrooms   
117909        62        51    Wyoming      state       nan  All Bedrooms   
117910        62        51    Wyoming      state       nan  All Bedrooms   
117911        62        51    Wyoming      state       nan  All Bedrooms   

                    Home Type        Date  \
0       all homes (SFR/condo)  2000-01-31   
1       all homes (SFR/condo)  2000-02-29   
2       all homes (SFR/condo)  2000-03-31   
3       all homes (SFR/condo)  2000-04-30   
4       all homes (SFR/condo)  2000-05-31   
...                       ...         ...   
117907                  condo  2023-09-30   
117908                  condo  2023-10-31   
117909                  condo  2023-11-30   
117910                  condo  2023-12-31   
117911                  condo  2024-01-31   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                         81310.639504   
1                                         80419.761984   
2                                         80480.449461   
3                                         79799.206525   
4                                         79666.469861   
...                                                ...   
117907                                   486974.735908   
117908                                   485847.539614   
117909                                   484223.885775   
117910                                   481522.403338   
117911                                   481181.718200   

        Bottom Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                                   ...   
117907                                                NaN   
117908                                                NaN   
117909                                                NaN   
117910                                                NaN   
117911                                                NaN   

        Top Tier ZHVI (Smoothed) (Seasonally Adjusted)  
0                                                  NaN  
1                                                  NaN  
2                                                  NaN  
3                                                  NaN  
4                                                  NaN  
...                                                ...  
117907                                             NaN  
117908                                             NaN  
117909                                             NaN  
117910                                             NaN  
117911                                             NaN  

[117912 rows x 11 columns]

In [11]:
final_df = combined_df

for index, row in final_df.iterrows():
    if row["RegionType"] == "city":
        final_df.at[index, "City"] = row["RegionName"]
    elif row["RegionType"] == "county":
        final_df.at[index, "County"] = row["RegionName"]
    if row["RegionType"] == "state":
        final_df.at[index, "StateName"] = row["RegionName"]

# coalesce State and StateName columns
# final_df["State"] = final_df["State"].combine_first(final_df["StateName"])
# final_df["County"] = final_df["County"].combine_first(final_df["CountyName"])

# final_df = final_df.drop(
#     columns=[
#         "StateName",
#         # "CountyName"
#     ]
# )
final_df

RegionID  SizeRank RegionName RegionType StateName Bedroom Count  \
0              3        48     Alaska      state    Alaska    1-Bedrooms   
1              3        48     Alaska      state    Alaska    1-Bedrooms   
2              3        48     Alaska      state    Alaska    1-Bedrooms   
3              3        48     Alaska      state    Alaska    1-Bedrooms   
4              3        48     Alaska      state    Alaska    1-Bedrooms   
...          ...       ...        ...        ...       ...           ...   
117907        62        51    Wyoming      state   Wyoming  All Bedrooms   
117908        62        51    Wyoming      state   Wyoming  All Bedrooms   
117909        62        51    Wyoming      state   Wyoming  All Bedrooms   
117910        62        51    Wyoming      state   Wyoming  All Bedrooms   
117911        62        51    Wyoming      state   Wyoming  All Bedrooms   

                    Home Type        Date  \
0       all homes (SFR/condo)  2000-01-31   
1       all homes (SFR/condo)  2000-02-29   
2       all homes (SFR/condo)  2000-03-31   
3       all homes (SFR/condo)  2000-04-30   
4       all homes (SFR/condo)  2000-05-31   
...                       ...         ...   
117907                  condo  2023-09-30   
117908                  condo  2023-10-31   
117909                  condo  2023-11-30   
117910                  condo  2023-12-31   
117911                  condo  2024-01-31   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                  NaN   
1                                                  NaN   
2                                                  NaN   
3                                                  NaN   
4                                                  NaN   
...                                                ...   
117907                                             NaN   
117908                                             NaN   
117909                                             NaN   
117910                                             NaN   
117911                                             NaN   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)_1  \
0                                                    NaN   
1                                                    NaN   
2                                                    NaN   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
117907                                               NaN   
117908                                               NaN   
117909                                               NaN   
117910                                               NaN   
117911                                               NaN   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)_2  \
0                                                    NaN   
1                                                    NaN   
2                                                    NaN   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
117907                                               NaN   
117908                                               NaN   
117909                                               NaN   
117910                                               NaN   
117911                                               NaN   

        Bottom Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                              

In [12]:
final_df = final_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
        "StateCodeFIPS": "State Code FIPS",
        "StateName": "State",
        "MunicipalCodeFIPS": "Municipal Code FIPS",
    }
)

final_df

Region ID  Size Rank   Region Region Type    State Bedroom Count  \
0               3         48   Alaska       state   Alaska    1-Bedrooms   
1               3         48   Alaska       state   Alaska    1-Bedrooms   
2               3         48   Alaska       state   Alaska    1-Bedrooms   
3               3         48   Alaska       state   Alaska    1-Bedrooms   
4               3         48   Alaska       state   Alaska    1-Bedrooms   
...           ...        ...      ...         ...      ...           ...   
117907         62         51  Wyoming       state  Wyoming  All Bedrooms   
117908         62         51  Wyoming       state  Wyoming  All Bedrooms   
117909         62         51  Wyoming       state  Wyoming  All Bedrooms   
117910         62         51  Wyoming       state  Wyoming  All Bedrooms   
117911         62         51  Wyoming       state  Wyoming  All Bedrooms   

                    Home Type        Date  \
0       all homes (SFR/condo)  2000-01-31   
1       all homes (SFR/condo)  2000-02-29   
2       all homes (SFR/condo)  2000-03-31   
3       all homes (SFR/condo)  2000-04-30   
4       all homes (SFR/condo)  2000-05-31   
...                       ...         ...   
117907                  condo  2023-09-30   
117908                  condo  2023-10-31   
117909                  condo  2023-11-30   
117910                  condo  2023-12-31   
117911                  condo  2024-01-31   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                  NaN   
1                                                  NaN   
2                                                  NaN   
3                                                  NaN   
4                                                  NaN   
...                                                ...   
117907                                             NaN   
117908                                             NaN   
117909                                             NaN   
117910                                             NaN   
117911                                             NaN   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)_1  \
0                                                    NaN   
1                                                    NaN   
2                                                    NaN   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
117907                                               NaN   
117908                                               NaN   
117909                                               NaN   
117910                                               NaN   
117911                                               NaN   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)_2  \
0                                                    NaN   
1                                                    NaN   
2                                                    NaN   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
117907                                               NaN   
117908                                               NaN   
117909                                               NaN   
117910                                               NaN   
117911                                               NaN   

        Bottom Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                              

In [13]:
save_final_df_as_jsonl(FULL_PROCESSED_DIR_PATH, final_df)